In [122]:
import numpy as np
import random
from sklearn import decomposition
from typing import List
np.set_printoptions(precision=4)
np.set_printoptions(suppress=True)

In [142]:
def create_groups_of_equivalent_vectors(num_groups = 300, group_size = 20, dim = 1000, noise = False) -> List[np.ndarray]:
    
    """
    Return: groups, a list of numpy arrays, each representing one groups of vectors that share
            the syntactic component. 
            groups[i][j,k] is the kth coordinate in the jth vector in the ith group.
    """
    groups = []
    random.seed(0)
    for i in range(num_groups):
        
        group = []
        
        shared_component = random.choice(range(0,100)) # The "syntactic" component that is shared for this group
    
        for j in range(group_size):
            
            semantic_component = random.choice(range(0,100)) # the "semantic" component
            
            vec = np.random.rand(dim) * 0.01 # small noise in all other coordinates
            vec[0] = shared_component
            
            if noise: 
                
                vec[0] += random.random() - 0.5
                
            vec[1] = semantic_component
            
            group.append(vec)
        
        groups.append(np.array(group, dtype = float))
    
    return groups
             

def find_basis_to_shared_subspace(groups, init_pca_dim = 50, semantic_space_dim = 25, syntactic_space_dim = 2):
    
    # Perform initial PCA on all vectors
    
    all_vectors = [vec for group in groups for vec in group]
    init_pca = decomposition.PCA(n_components = init_pca_dim)
    init_pca.fit(all_vectors)
    all_vectors = init_pca.inverse_transform(init_pca.transform(all_vectors))
    
    data = []
    denoised_groups = []
    
    # substract the mean from each group (after initial PCA).
    
    for group in groups:
        
        denoised_group = init_pca.inverse_transform(init_pca.transform(group)) # (group_size, dim)
        denoised_groups.append(denoised_group)
        mean = np.mean(denoised_group, axis = 0) # array of shape (dim, )
        mean_substracted_group = denoised_group - mean
        
        for vec in mean_substracted_group:
            
            data.append(vec)
    
    # perform PCA on the mean-substracted groups to recover the "semantic" basis
    
    semantic_pca = decomposition.PCA(n_components = semantic_space_dim)
    semantic_pca.fit(data)
    
    # remove the semantic data from each vector:
    
    sytactic_groups = []
    
    for group in denoised_groups:
        
        semantic_components = semantic_pca.inverse_transform(semantic_pca.transform(group)) # (group_size, dim)
        raw_syntactic_components = group - semantic_components # (group_size, dim)
        sytactic_groups.append(raw_syntactic_components)
    
    # perform a final PCA to get the syntactic components
    
    all_syntactic_vectors = [v for group in sytactic_groups for v in group]
    syntactic_pca = decomposition.PCA(n_components = semantic_space_dim)
    syntactic_pca.fit(all_syntactic_vectors)
    
    # apply the final pca
    
    for i,group in enumerate(sytactic_groups):
        
        sytactic_groups[i] = syntactic_pca.inverse_transform(syntactic_pca.transform(group))
    
    return sytactic_groups
        
    
def compare(groups_before, groups_after):
    
    for i, (original, transformed) in enumerate(zip(groups_before, groups_after)):
        
        print("=============================================================")
        print("Group number {}".format(i))
        
        for j, (v,v2) in enumerate(zip(original, transformed)):
            print("Vector {} in the group:".format(j))
            print("Before: ", np.round(v[:5], decimals = 3), "After: ", np.round(v2[:5], decimals = 3))
    

First, perform an experiment without any noise in the "syntactic" (shared) coordinate.

In [140]:
groups = create_groups_of_equivalent_vectors(num_groups = 300, group_size = 50, noise = False)
groups_in_syntactic_subspace = find_basis_to_shared_subspace(groups)
compare(groups, groups_in_syntactic_subspace)

Group number 0
Vector 0 in the group:
Before:  [49.    97.     0.009  0.003  0.003] After:  [49.     0.     0.003  0.005  0.005]
Vector 1 in the group:
Before:  [49.    53.     0.003  0.     0.005] After:  [49.     0.     0.004  0.005  0.004]
Vector 2 in the group:
Before:  [49.     5.     0.001  0.008  0.005] After:  [49.     0.     0.005  0.005  0.005]
Vector 3 in the group:
Before:  [49.    33.     0.009  0.002  0.   ] After:  [49.     0.     0.004  0.005  0.005]
Vector 4 in the group:
Before:  [49.    65.     0.006  0.009  0.006] After:  [49.     0.     0.004  0.005  0.005]
Vector 5 in the group:
Before:  [49.    62.     0.006  0.008  0.008] After:  [49.     0.     0.004  0.005  0.005]
Vector 6 in the group:
Before:  [49.    51.     0.005  0.005  0.   ] After:  [49.     0.     0.003  0.004  0.005]
Vector 7 in the group:
Before:  [49.    38.     0.003  0.006  0.002] After:  [49.     0.     0.004  0.005  0.005]
Vector 8 in the group:
Before:  [49.    61.     0.006  0.006  0.005] Afte

Before:  [89.    71.     0.005  0.     0.007] After:  [89.     0.     0.004  0.005  0.006]
Vector 5 in the group:
Before:  [89.    77.     0.006  0.004  0.002] After:  [89.     0.     0.004  0.005  0.005]
Vector 6 in the group:
Before:  [89.    96.     0.005  0.007  0.006] After:  [89.     0.     0.005  0.005  0.005]
Vector 7 in the group:
Before:  [89.     0.     0.003  0.009  0.002] After:  [89.     0.     0.003  0.004  0.004]
Vector 8 in the group:
Before:  [89.     4.     0.001  0.002  0.003] After:  [89.     0.     0.004  0.004  0.004]
Vector 9 in the group:
Before:  [89.    63.     0.005  0.001  0.005] After:  [89.     0.     0.004  0.005  0.005]
Vector 10 in the group:
Before:  [89.    41.     0.005  0.004  0.009] After:  [89.     0.     0.004  0.005  0.006]
Vector 11 in the group:
Before:  [89.    39.     0.007  0.006  0.009] After:  [89.     0.     0.003  0.005  0.006]
Vector 12 in the group:
Before:  [89.    59.     0.01   0.004  0.001] After:  [89.     0.     0.004  0.005  0

Before:  [63.     2.     0.001  0.004  0.001] After:  [63.     0.     0.004  0.004  0.005]
Vector 39 in the group:
Before:  [63.     4.     0.003  0.     0.008] After:  [63.     0.     0.003  0.004  0.006]
Vector 40 in the group:
Before:  [63.    76.     0.009  0.002  0.007] After:  [63.     0.     0.005  0.005  0.006]
Vector 41 in the group:
Before:  [63.    79.     0.001  0.002  0.008] After:  [63.     0.     0.004  0.005  0.006]
Vector 42 in the group:
Before:  [63.    16.     0.007  0.004  0.003] After:  [63.     0.     0.004  0.004  0.005]
Vector 43 in the group:
Before:  [63.    80.     0.003  0.002  0.006] After:  [63.     0.     0.003  0.004  0.005]
Vector 44 in the group:
Before:  [63.    41.     0.009  0.008  0.007] After:  [63.     0.     0.004  0.005  0.005]
Vector 45 in the group:
Before:  [63.    13.     0.002  0.001  0.008] After:  [63.     0.     0.003  0.004  0.004]
Vector 46 in the group:
Before:  [63.    89.     0.008  0.007  0.005] After:  [63.     0.     0.004  0.0

Before:  [37.    15.     0.004  0.005  0.007] After:  [37.     0.     0.004  0.005  0.006]
Vector 9 in the group:
Before:  [37.    48.     0.005  0.005  0.003] After:  [37.     0.     0.004  0.004  0.004]
Vector 10 in the group:
Before:  [37.    51.     0.005  0.004  0.003] After:  [37.     0.     0.003  0.005  0.005]
Vector 11 in the group:
Before:  [37.    75.     0.01   0.001  0.006] After:  [37.     0.     0.004  0.005  0.005]
Vector 12 in the group:
Before:  [37.    59.     0.007  0.003  0.009] After:  [37.     0.     0.004  0.004  0.005]
Vector 13 in the group:
Before:  [37.    17.     0.005  0.003  0.004] After:  [37.     0.     0.005  0.005  0.004]
Vector 14 in the group:
Before:  [37.    71.     0.003  0.001  0.004] After:  [37.     0.     0.004  0.005  0.004]
Vector 15 in the group:
Before:  [37.    85.     0.002  0.002  0.004] After:  [37.     0.     0.004  0.005  0.004]
Vector 16 in the group:
Before:  [37.    38.     0.003  0.007  0.003] After:  [37.     0.     0.004  0.00

Before:  [61.    17.     0.004  0.009  0.009] After:  [61.     0.     0.004  0.004  0.005]
Vector 19 in the group:
Before:  [61.    97.     0.009  0.006  0.001] After:  [61.     0.     0.004  0.006  0.004]
Vector 20 in the group:
Before:  [61.    26.     0.005  0.003  0.007] After:  [61.     0.     0.004  0.005  0.005]
Vector 21 in the group:
Before:  [61.    99.     0.005  0.001  0.004] After:  [61.     0.     0.003  0.004  0.005]
Vector 22 in the group:
Before:  [61.    63.     0.008  0.009  0.003] After:  [61.     0.     0.003  0.004  0.005]
Vector 23 in the group:
Before:  [61.    72.     0.01   0.007  0.003] After:  [61.     0.     0.004  0.005  0.005]
Vector 24 in the group:
Before:  [61.    98.     0.004  0.01   0.001] After:  [61.     0.     0.004  0.005  0.005]
Vector 25 in the group:
Before:  [61.    89.     0.007  0.001  0.005] After:  [61.     0.     0.003  0.004  0.004]
Vector 26 in the group:
Before:  [61.    27.     0.005  0.006  0.009] After:  [61.     0.     0.004  0.0

...

Before:  [34.    28.     0.009  0.003  0.004] After:  [34.     0.     0.005  0.005  0.005]
Vector 27 in the group:
Before:  [34.    13.     0.01   0.001  0.003] After:  [34.     0.     0.003  0.005  0.006]
Vector 28 in the group:
Before:  [34.    57.     0.002  0.007  0.006] After:  [34.     0.     0.004  0.004  0.005]
Vector 29 in the group:
Before:  [34.    69.     0.     0.009  0.007] After:  [34.     0.     0.004  0.004  0.005]
Vector 30 in the group:
Before:  [34.    21.     0.006  0.008  0.004] After:  [34.     0.     0.003  0.004  0.005]
Vector 31 in the group:
Before:  [34.    87.     0.004  0.005  0.001] After:  [34.     0.     0.004  0.005  0.004]
Vector 32 in the group:
Before:  [34.    77.     0.004  0.006  0.008] After:  [34.     0.     0.004  0.005  0.006]
Vector 33 in the group:
Before:  [34.    68.     0.005  0.008  0.003] After:  [34.     0.     0.005  0.006  0.005]
Vector 34 in the group:
Before:  [34.    18.     0.001  0.009  0.009] After:  [34.     0.     0.003  0.0

Before:  [86.    10.     0.     0.002  0.001] After:  [86.     0.     0.004  0.004  0.004]
Vector 41 in the group:
Before:  [86.    34.     0.     0.005  0.007] After:  [86.     0.     0.004  0.004  0.005]
Vector 42 in the group:
Before:  [86.    24.     0.008  0.004  0.003] After:  [86.     0.     0.004  0.005  0.005]
Vector 43 in the group:
Before:  [86.    20.     0.003  0.001  0.009] After:  [86.     0.     0.004  0.005  0.004]
Vector 44 in the group:
Before:  [86.    70.     0.01   0.001  0.009] After:  [86.     0.     0.004  0.005  0.004]
Vector 45 in the group:
Before:  [86.    63.     0.007  0.003  0.   ] After:  [86.     0.     0.004  0.005  0.005]
Vector 46 in the group:
Before:  [86.     9.     0.003  0.009  0.009] After:  [86.     0.     0.004  0.005  0.005]
Vector 47 in the group:
Before:  [86.    59.     0.006  0.001  0.005] After:  [86.     0.     0.004  0.004  0.005]
Vector 48 in the group:
Before:  [86.    73.     0.008  0.002  0.006] After:  [86.     0.     0.004  0.0

Before:  [21.    37.     0.     0.005  0.006] After:  [21.     0.     0.004  0.004  0.005]
Vector 16 in the group:
Before:  [21.    47.     0.008  0.007  0.001] After:  [21.     0.     0.005  0.005  0.005]
Vector 17 in the group:
Before:  [21.    20.     0.     0.004  0.01 ] After:  [21.     0.     0.004  0.005  0.004]
Vector 18 in the group:
Before:  [21.     3.     0.     0.003  0.006] After:  [21.     0.     0.003  0.005  0.005]
Vector 19 in the group:
Before:  [21.     8.     0.007  0.007  0.004] After:  [21.     0.     0.004  0.004  0.005]
Vector 20 in the group:
Before:  [21.    50.     0.     0.01   0.003] After:  [21.     0.     0.004  0.004  0.005]
Vector 21 in the group:
Before:  [21.    57.     0.001  0.005  0.009] After:  [21.     0.     0.003  0.005  0.006]
Vector 22 in the group:
Before:  [21.    28.     0.004  0.     0.007] After:  [21.     0.     0.004  0.005  0.005]
Vector 23 in the group:
Before:  [21.    30.     0.003  0.006  0.005] After:  [21.     0.     0.004  0.0

Before:  [26.    22.     0.01   0.009  0.003] After:  [26.     0.     0.004  0.005  0.006]
Vector 43 in the group:
Before:  [26.    14.     0.002  0.004  0.006] After:  [26.     0.     0.003  0.005  0.005]
Vector 44 in the group:
Before:  [26.    68.     0.004  0.006  0.01 ] After:  [26.     0.     0.004  0.005  0.005]
Vector 45 in the group:
Before:  [26.    64.     0.005  0.006  0.001] After:  [26.     0.     0.004  0.005  0.005]
Vector 46 in the group:
Before:  [26.    86.     0.005  0.006  0.002] After:  [26.     0.     0.005  0.004  0.004]
Vector 47 in the group:
Before:  [26.    32.     0.008  0.008  0.005] After:  [26.     0.     0.005  0.005  0.006]
Vector 48 in the group:
Before:  [26.    56.     0.008  0.008  0.001] After:  [26.     0.     0.004  0.005  0.006]
Vector 49 in the group:
Before:  [26.    66.     0.008  0.003  0.003] After:  [26.     0.     0.004  0.005  0.006]
Group number 292
Vector 0 in the group:
Before:  [54.    79.     0.008  0.005  0.008] After:  [54.     0

Before:  [ 4.    98.     0.006  0.006  0.005] After:  [4.    0.    0.003 0.005 0.006]
Vector 49 in the group:
Before:  [ 4.    72.     0.002  0.006  0.007] After:  [4.    0.    0.004 0.004 0.004]


Repeat the experiment, with **a noise of ± 0.5 for each point** in the syntactic coordinate.

In [145]:
groups = create_groups_of_equivalent_vectors(num_groups = 300, group_size = 50, noise = True)
groups_in_syntactic_subspace = find_basis_to_shared_subspace(groups, semantic_space_dim = 1, syntactic_space_dim = 1)
compare(groups, groups_in_syntactic_subspace)

Group number 0
Vector 0 in the group:
Before:  [49.39  97.     0.002  0.004  0.002] After:  [49.401  0.006  0.005  0.005  0.005]
Vector 1 in the group:
Before:  [48.759  5.     0.002  0.003  0.009] After:  [48.759  0.006  0.005  0.005  0.005]
Vector 2 in the group:
Before:  [48.986 65.     0.004  0.001  0.006] After:  [48.993  0.006  0.005  0.005  0.005]
Vector 3 in the group:
Before:  [49.468 38.     0.003  0.007  0.003] After:  [49.472  0.006  0.005  0.005  0.005]
Vector 4 in the group:
Before:  [49.083 45.     0.004  0.007  0.005] After:  [49.088  0.006  0.005  0.005  0.005]
Vector 5 in the group:
Before:  [49.005 27.     0.005  0.005  0.008] After:  [49.008  0.006  0.005  0.005  0.005]
Vector 6 in the group:
Before:  [48.64  36.     0.01   0.006  0.005] After:  [48.644  0.006  0.005  0.005  0.005]
Vector 7 in the group:
Before:  [49.118 12.     0.002  0.006  0.   ] After:  [49.12   0.006  0.005  0.005  0.005]
Vector 8 in the group:
Before:  [49.487 32.     0.007  0.002  0.   ] Afte

Vector 7 in the group:
Before:  [23.093 23.     0.     0.008  0.009] After:  [23.096  0.003  0.005  0.005  0.005]
Vector 8 in the group:
Before:  [22.603 10.     0.003  0.005  0.   ] After:  [22.604  0.003  0.005  0.005  0.005]
Vector 9 in the group:
Before:  [22.808 74.     0.01   0.005  0.004] After:  [22.816  0.003  0.005  0.005  0.005]
Vector 10 in the group:
Before:  [23.398 48.     0.006  0.01   0.008] After:  [23.403  0.003  0.005  0.005  0.005]
Vector 11 in the group:
Before:  [23.304 16.     0.008  0.002  0.007] After:  [23.306  0.003  0.005  0.005  0.005]
Vector 12 in the group:
Before:  [23.008 40.     0.004  0.01   0.004] After:  [23.013  0.003  0.005  0.005  0.005]
Vector 13 in the group:
Before:  [23.255 30.     0.005  0.002  0.007] After:  [23.258  0.003  0.005  0.005  0.005]
Vector 14 in the group:
Before:  [22.872 37.     0.005  0.003  0.008] After:  [22.877  0.003  0.005  0.005  0.005]
Vector 15 in the group:
Before:  [22.546 84.     0.002  0.009  0.006] After:  [22.5

Before:  [16.21  72.     0.006  0.008  0.007] After:  [16.219  0.002  0.005  0.005  0.005]
Vector 1 in the group:
Before:  [16.322 41.     0.002  0.006  0.002] After:  [16.327  0.002  0.005  0.005  0.005]
Vector 2 in the group:
Before:  [15.974 50.     0.001  0.006  0.001] After:  [15.979  0.002  0.005  0.005  0.005]
Vector 3 in the group:
Before:  [15.635 66.     0.004  0.01   0.009] After:  [15.643  0.002  0.005  0.005  0.005]
Vector 4 in the group:
Before:  [16.066 10.     0.003  0.009  0.007] After:  [16.067  0.002  0.005  0.005  0.005]
Vector 5 in the group:
Before:  [15.861 44.     0.01   0.006  0.002] After:  [15.866  0.002  0.005  0.005  0.005]
Vector 6 in the group:
Before:  [15.691  8.     0.003  0.     0.009] After:  [15.692  0.002  0.005  0.005  0.005]
Vector 7 in the group:
Before:  [16.171 14.     0.006  0.007  0.001] After:  [16.173  0.002  0.005  0.005  0.005]
Vector 8 in the group:
Before:  [15.543 60.     0.002  0.01   0.007] After:  [15.55   0.002  0.005  0.005  0.00

Before:  [57.099 62.     0.006  0.003  0.008] After:  [57.106  0.006  0.005  0.005  0.005]
Vector 16 in the group:
Before:  [57.469 19.     0.006  0.004  0.006] After:  [57.471  0.007  0.005  0.005  0.005]
Vector 17 in the group:
Before:  [57.184 66.     0.003  0.006  0.007] After:  [57.192  0.006  0.005  0.005  0.005]
Vector 18 in the group:
Before:  [56.8   24.     0.004  0.004  0.008] After:  [56.803  0.006  0.005  0.005  0.005]
Vector 19 in the group:
Before:  [57.131 66.     0.003  0.001  0.003] After:  [57.138  0.006  0.005  0.005  0.005]
Vector 20 in the group:
Before:  [57.446 15.     0.01   0.001  0.   ] After:  [57.448  0.006  0.005  0.005  0.005]
Vector 21 in the group:
Before:  [56.843 19.     0.005  0.002  0.007] After:  [56.845  0.006  0.005  0.005  0.005]
Vector 22 in the group:
Before:  [57.37  42.     0.     0.008  0.005] After:  [57.375  0.006  0.005  0.005  0.005]
Vector 23 in the group:
Before:  [57.266 20.     0.009  0.01   0.004] After:  [57.268  0.006  0.005  0.0

Before:  [68.643  9.     0.007  0.006  0.001] After:  [68.644  0.008  0.005  0.005  0.005]
Vector 30 in the group:
Before:  [68.884  4.     0.007  0.006  0.004] After:  [68.884  0.008  0.005  0.005  0.005]
Vector 31 in the group:
Before:  [68.616 72.     0.     0.001  0.007] After:  [68.624  0.008  0.005  0.005  0.005]
Vector 32 in the group:
Before:  [69.024  8.     0.     0.005  0.007] After:  [69.025  0.008  0.005  0.005  0.005]
Vector 33 in the group:
Before:  [68.803 72.     0.005  0.005  0.002] After:  [68.811  0.008  0.005  0.005  0.005]
Vector 34 in the group:
Before:  [69.369 85.     0.001  0.007  0.008] After:  [69.379  0.008  0.005  0.005  0.005]
Vector 35 in the group:
Before:  [68.902 61.     0.003  0.001  0.01 ] After:  [68.909  0.008  0.005  0.005  0.005]
Vector 36 in the group:
Before:  [69.244 40.     0.009  0.001  0.01 ] After:  [69.248  0.008  0.005  0.005  0.005]
Vector 37 in the group:
Before:  [68.967 79.     0.004  0.01   0.003] After:  [68.976  0.008  0.005  0.0

...

Before:  [82.431 88.     0.004  0.003  0.008] After:  [82.441  0.009  0.005  0.005  0.005]
Vector 16 in the group:
Before:  [81.741  8.     0.005  0.007  0.007] After:  [81.742  0.009  0.005  0.005  0.005]
Vector 17 in the group:
Before:  [82.365 70.     0.009  0.009  0.006] After:  [82.373  0.009  0.005  0.005  0.005]
Vector 18 in the group:
Before:  [81.576 29.     0.01   0.001  0.008] After:  [81.579  0.009  0.005  0.005  0.005]
Vector 19 in the group:
Before:  [81.527 27.     0.002  0.005  0.009] After:  [81.53   0.009  0.005  0.005  0.005]
Vector 20 in the group:
Before:  [81.516 66.     0.008  0.004  0.007] After:  [81.523  0.009  0.005  0.005  0.005]
Vector 21 in the group:
Before:  [81.802 37.     0.008  0.007  0.001] After:  [81.806  0.009  0.005  0.005  0.005]
Vector 22 in the group:
Before:  [82.034 54.     0.009  0.008  0.01 ] After:  [82.04   0.009  0.005  0.005  0.005]
Vector 23 in the group:
Before:  [81.57  47.     0.004  0.003  0.004] After:  [81.575  0.009  0.005  0.0

Before:  [28.124 77.     0.003  0.002  0.001] After:  [28.133  0.003  0.005  0.005  0.005]
Vector 13 in the group:
Before:  [27.758 52.     0.004  0.     0.007] After:  [27.764  0.003  0.005  0.005  0.005]
Vector 14 in the group:
Before:  [27.677 46.     0.004  0.003  0.01 ] After:  [27.682  0.003  0.005  0.005  0.005]
Vector 15 in the group:
Before:  [28.228 21.     0.001  0.005  0.007] After:  [28.23   0.003  0.005  0.005  0.005]
Vector 16 in the group:
Before:  [28.35  54.     0.005  0.004  0.001] After:  [28.356  0.003  0.005  0.005  0.005]
Vector 17 in the group:
Before:  [27.627  9.     0.008  0.007  0.003] After:  [27.628  0.003  0.005  0.005  0.005]
Vector 18 in the group:
Before:  [27.684  7.     0.01   0.009  0.004] After:  [27.685  0.003  0.005  0.005  0.005]
Vector 19 in the group:
Before:  [28.35  48.     0.004  0.009  0.009] After:  [28.355  0.003  0.005  0.005  0.005]
Vector 20 in the group:
Before:  [28.389 25.     0.006  0.009  0.005] After:  [28.392  0.003  0.005  0.0

Before:  [91.695 68.     0.     0.001  0.006] After:  [91.703  0.01   0.005  0.005  0.005]
Vector 2 in the group:
Before:  [92.131 22.     0.005  0.003  0.01 ] After:  [92.134  0.01   0.005  0.005  0.005]
Vector 3 in the group:
Before:  [92.384 14.     0.01   0.005  0.002] After:  [92.385  0.01   0.005  0.005  0.005]
Vector 4 in the group:
Before:  [91.779 99.     0.006  0.006  0.008] After:  [91.79   0.01   0.005  0.005  0.005]
Vector 5 in the group:
Before:  [91.798 27.     0.01   0.008  0.005] After:  [91.801  0.01   0.005  0.005  0.005]
Vector 6 in the group:
Before:  [92.499  3.     0.008  0.007  0.006] After:  [92.5    0.01   0.005  0.005  0.005]
Vector 7 in the group:
Before:  [92.172 70.     0.001  0.004  0.009] After:  [92.179  0.01   0.005  0.005  0.005]
Vector 8 in the group:
Before:  [92.152 89.     0.009  0.005  0.002] After:  [92.162  0.01   0.005  0.005  0.005]
Vector 9 in the group:
Before:  [91.849 54.     0.008  0.002  0.007] After:  [91.855  0.01   0.005  0.005  0.00

Before:  [21.96  88.     0.009  0.004  0.008] After:  [21.97   0.002  0.005  0.005  0.005]
Vector 1 in the group:
Before:  [22.025 61.     0.002  0.004  0.01 ] After:  [22.032  0.002  0.005  0.005  0.005]
Vector 2 in the group:
Before:  [22.475 29.     0.001  0.01   0.009] After:  [22.479  0.003  0.005  0.005  0.005]
Vector 3 in the group:
Before:  [22.433  6.     0.001  0.001  0.002] After:  [22.433  0.003  0.005  0.005  0.005]
Vector 4 in the group:
Before:  [22.28   2.     0.006  0.     0.009] After:  [22.28   0.003  0.005  0.005  0.005]
Vector 5 in the group:
Before:  [22.193 63.     0.006  0.006  0.009] After:  [22.2    0.003  0.005  0.005  0.005]
Vector 6 in the group:
Before:  [21.848 28.     0.005  0.01   0.008] After:  [21.851  0.002  0.005  0.005  0.005]
Vector 7 in the group:
Before:  [21.658  0.     0.004  0.001  0.005] After:  [21.658  0.002  0.005  0.005  0.005]
Vector 8 in the group:
Before:  [22.195 93.     0.001  0.001  0.002] After:  [22.205  0.003  0.005  0.005  0.00

Before:  [ 5.36  35.     0.007  0.008  0.008] After:  [5.364 0.001 0.005 0.005 0.005]
Vector 9 in the group:
Before:  [ 5.371 41.     0.002  0.003  0.009] After:  [5.376 0.001 0.005 0.005 0.005]
Vector 10 in the group:
Before:  [ 4.592 58.     0.009  0.     0.005] After:  [4.599 0.001 0.005 0.005 0.005]
Vector 11 in the group:
Before:  [ 4.592 55.     0.005  0.009  0.006] After:  [4.598 0.001 0.005 0.005 0.005]
Vector 12 in the group:
Before:  [4.592 3.    0.004 0.005 0.007] After:  [4.592 0.001 0.005 0.005 0.005]
Vector 13 in the group:
Before:  [ 4.717 52.     0.001  0.005  0.   ] After:  [4.722 0.001 0.005 0.005 0.005]
Vector 14 in the group:
Before:  [ 5.194 28.     0.009  0.001  0.008] After:  [5.197 0.001 0.005 0.005 0.005]
Vector 15 in the group:
Before:  [ 5.329 60.     0.004  0.001  0.   ] After:  [5.336 0.001 0.005 0.005 0.005]
Vector 16 in the group:
Before:  [ 5.363 58.     0.006  0.008  0.006] After:  [5.369 0.001 0.005 0.005 0.005]
Vector 17 in the group:
Before:  [ 5.167

Repeat the experiment, with **a noise of ± 0.5 for each point** in the syntactic coordinate, and **with semantic_dim = 1**

In [146]:
groups = create_groups_of_equivalent_vectors(num_groups = 300, group_size = 50, noise = True)
groups_in_syntactic_subspace = find_basis_to_shared_subspace(groups, semantic_space_dim = 1, syntactic_space_dim = 1)
compare(groups, groups_in_syntactic_subspace)

Group number 0
Vector 0 in the group:
Before:  [49.39  97.     0.005  0.002  0.005] After:  [49.401  0.006  0.005  0.005  0.005]
Vector 1 in the group:
Before:  [48.759  5.     0.004  0.001  0.007] After:  [48.759  0.006  0.005  0.005  0.005]
Vector 2 in the group:
Before:  [48.986 65.     0.001  0.     0.004] After:  [48.993  0.006  0.005  0.005  0.005]
Vector 3 in the group:
Before:  [49.468 38.     0.009  0.002  0.002] After:  [49.472  0.006  0.005  0.005  0.005]
Vector 4 in the group:
Before:  [49.083 45.     0.002  0.003  0.008] After:  [49.088  0.006  0.005  0.005  0.005]
Vector 5 in the group:
Before:  [49.005 27.     0.009  0.007  0.003] After:  [49.008  0.006  0.005  0.005  0.005]
Vector 6 in the group:
Before:  [48.64  36.     0.004  0.007  0.005] After:  [48.644  0.006  0.005  0.005  0.005]
Vector 7 in the group:
Before:  [49.118 12.     0.007  0.008  0.009] After:  [49.12   0.006  0.005  0.005  0.005]
Vector 8 in the group:
Before:  [49.487 32.     0.006  0.01   0.006] Afte

Before:  [22.777 13.     0.     0.006  0.006] After:  [22.778  0.003  0.005  0.005  0.005]
Vector 32 in the group:
Before:  [23.106 71.     0.005  0.008  0.001] After:  [23.114  0.003  0.005  0.005  0.005]
Vector 33 in the group:
Before:  [23.296 19.     0.008  0.005  0.005] After:  [23.298  0.003  0.005  0.005  0.005]
Vector 34 in the group:
Before:  [23.428 57.     0.007  0.001  0.   ] After:  [23.435  0.003  0.005  0.005  0.005]
Vector 35 in the group:
Before:  [23.268 23.     0.003  0.004  0.007] After:  [23.27   0.003  0.005  0.005  0.005]
Vector 36 in the group:
Before:  [22.675 55.     0.003  0.003  0.005] After:  [22.681  0.003  0.005  0.005  0.005]
Vector 37 in the group:
Before:  [22.84  58.     0.005  0.005  0.006] After:  [22.847  0.003  0.005  0.005  0.005]
Vector 38 in the group:
Before:  [22.643 66.     0.     0.01   0.005] After:  [22.65   0.003  0.005  0.005  0.005]
Vector 39 in the group:
Before:  [23.132 59.     0.004  0.005  0.003] After:  [23.138  0.003  0.005  0.0

Before:  [15.647 76.     0.002  0.002  0.002] After:  [15.656  0.002  0.005  0.005  0.005]
Vector 14 in the group:
Before:  [16.011 39.     0.01   0.001  0.006] After:  [16.016  0.002  0.005  0.005  0.005]
Vector 15 in the group:
Before:  [15.625 20.     0.004  0.001  0.002] After:  [15.628  0.002  0.005  0.005  0.005]
Vector 16 in the group:
Before:  [16.411 17.     0.004  0.006  0.   ] After:  [16.413  0.002  0.005  0.005  0.005]
Vector 17 in the group:
Before:  [16.142 90.     0.007  0.005  0.002] After:  [16.152  0.002  0.005  0.005  0.005]
Vector 18 in the group:
Before:  [16.224 97.     0.     0.003  0.008] After:  [16.235  0.002  0.005  0.005  0.005]
Vector 19 in the group:
Before:  [16.324 93.     0.007  0.009  0.002] After:  [16.334  0.002  0.005  0.005  0.005]
Vector 20 in the group:
Before:  [16.323  5.     0.005  0.002  0.01 ] After:  [16.324  0.002  0.005  0.005  0.005]
Vector 21 in the group:
Before:  [16.244 88.     0.002  0.     0.003] After:  [16.254  0.002  0.005  0.0

Before:  [57.344 77.     0.004  0.005  0.006] After:  [57.352  0.006  0.005  0.005  0.005]
Vector 40 in the group:
Before:  [57.231 71.     0.004  0.009  0.   ] After:  [57.239  0.006  0.005  0.005  0.005]
Vector 41 in the group:
Before:  [56.544  0.     0.009  0.     0.002] After:  [56.544  0.006  0.005  0.005  0.005]
Vector 42 in the group:
Before:  [56.743 17.     0.001  0.     0.001] After:  [56.745  0.006  0.005  0.005  0.005]
Vector 43 in the group:
Before:  [57.11  86.     0.007  0.001  0.008] After:  [57.12   0.006  0.005  0.005  0.005]
Vector 44 in the group:
Before:  [57.185 84.     0.     0.006  0.009] After:  [57.194  0.006  0.005  0.005  0.005]
Vector 45 in the group:
Before:  [57.016 96.     0.008  0.001  0.009] After:  [57.027  0.006  0.005  0.005  0.005]
Vector 46 in the group:
Before:  [57.134 82.     0.009  0.009  0.007] After:  [57.143  0.006  0.005  0.005  0.005]
Vector 47 in the group:
Before:  [57.385 36.     0.007  0.008  0.003] After:  [57.389  0.006  0.005  0.0

Before:  [22.788 89.     0.004  0.009  0.008] After:  [22.798  0.003  0.005  0.005  0.005]
Vector 12 in the group:
Before:  [22.984 74.     0.006  0.009  0.004] After:  [22.992  0.003  0.005  0.005  0.005]
Vector 13 in the group:
Before:  [23.207  3.     0.003  0.004  0.008] After:  [23.208  0.003  0.005  0.005  0.005]
Vector 14 in the group:
Before:  [23.1   79.     0.002  0.01   0.008] After:  [23.109  0.003  0.005  0.005  0.005]
Vector 15 in the group:
Before:  [22.673 85.     0.     0.002  0.005] After:  [22.683  0.003  0.005  0.005  0.005]
Vector 16 in the group:
Before:  [22.815 56.     0.     0.005  0.006] After:  [22.822  0.003  0.005  0.005  0.005]
Vector 17 in the group:
Before:  [23.478 41.     0.001  0.007  0.   ] After:  [23.483  0.003  0.005  0.005  0.005]
Vector 18 in the group:
Before:  [23.269 72.     0.002  0.005  0.007] After:  [23.278  0.003  0.005  0.005  0.005]
Vector 19 in the group:
Before:  [22.644 80.     0.01   0.001  0.008] After:  [22.653  0.003  0.005  0.0

...

Before:  [93.397 85.     0.009  0.006  0.009] After:  [93.406  0.011  0.005  0.005  0.005]
Vector 29 in the group:
Before:  [92.593 82.     0.01   0.003  0.001] After:  [92.602  0.01   0.005  0.005  0.005]
Vector 30 in the group:
Before:  [92.863  7.     0.     0.004  0.002] After:  [92.864  0.011  0.005  0.005  0.005]
Vector 31 in the group:
Before:  [92.94  13.     0.005  0.001  0.001] After:  [92.942  0.011  0.005  0.005  0.005]
Vector 32 in the group:
Before:  [93.473 67.     0.008  0.007  0.001] After:  [93.481  0.011  0.005  0.005  0.005]
Vector 33 in the group:
Before:  [93.417 70.     0.009  0.005  0.001] After:  [93.425  0.011  0.005  0.005  0.005]
Vector 34 in the group:
Before:  [93.256  0.     0.004  0.01   0.005] After:  [93.256  0.011  0.005  0.005  0.005]
Vector 35 in the group:
Before:  [92.634 82.     0.     0.001  0.01 ] After:  [92.643  0.01   0.005  0.005  0.005]
Vector 36 in the group:
Before:  [92.981 22.     0.006  0.     0.008] After:  [92.984  0.011  0.005  0.0

Before:  [59.141 26.     0.009  0.005  0.008] After:  [59.144  0.007  0.005  0.005  0.005]
Vector 6 in the group:
Before:  [58.512  3.     0.009  0.002  0.001] After:  [58.512  0.007  0.005  0.005  0.005]
Vector 7 in the group:
Before:  [58.857 45.     0.002  0.008  0.006] After:  [58.862  0.007  0.005  0.005  0.005]
Vector 8 in the group:
Before:  [58.862 34.     0.008  0.009  0.009] After:  [58.865  0.007  0.005  0.005  0.005]
Vector 9 in the group:
Before:  [58.767 99.     0.008  0.009  0.001] After:  [58.779  0.007  0.005  0.005  0.005]
Vector 10 in the group:
Before:  [59.299 19.     0.01   0.005  0.002] After:  [59.301  0.007  0.005  0.005  0.005]
Vector 11 in the group:
Before:  [59.211 14.     0.008  0.009  0.001] After:  [59.213  0.007  0.005  0.005  0.005]
Vector 12 in the group:
Before:  [58.873 41.     0.     0.009  0.005] After:  [58.877  0.007  0.005  0.005  0.005]
Vector 13 in the group:
Before:  [58.903  9.     0.01   0.009  0.002] After:  [58.904  0.007  0.005  0.005  

Before:  [ 2.494 76.     0.003  0.003  0.009] After:  [2.503 0.    0.005 0.005 0.005]
Vector 28 in the group:
Before:  [ 1.514 60.     0.007  0.003  0.004] After:  [1.52  0.    0.005 0.005 0.005]
Vector 29 in the group:
Before:  [ 1.672 22.     0.002  0.009  0.003] After:  [1.675 0.    0.005 0.005 0.005]
Vector 30 in the group:
Before:  [ 1.877 17.     0.008  0.005  0.006] After:  [1.879 0.    0.005 0.005 0.005]
Vector 31 in the group:
Before:  [ 2.186 88.     0.002  0.01   0.004] After:  [2.196 0.    0.005 0.005 0.005]
Vector 32 in the group:
Before:  [2.435 6.    0.009 0.009 0.006] After:  [2.435 0.    0.005 0.005 0.005]
Vector 33 in the group:
Before:  [ 1.795 41.     0.007  0.009  0.004] After:  [1.799 0.    0.005 0.005 0.005]
Vector 34 in the group:
Before:  [ 1.597 14.     0.004  0.007  0.008] After:  [1.599 0.    0.005 0.005 0.005]
Vector 35 in the group:
Before:  [ 2.493 12.     0.003  0.005  0.008] After:  [2.495 0.    0.005 0.005 0.005]
Vector 36 in the group:
Before:  [2.021

Before:  [33.537 19.     0.006  0.01   0.003] After:  [33.539  0.004  0.005  0.005  0.005]
Vector 2 in the group:
Before:  [33.954 57.     0.009  0.006  0.001] After:  [33.96   0.004  0.005  0.005  0.005]
Vector 3 in the group:
Before:  [33.502 74.     0.007  0.003  0.009] After:  [33.51   0.004  0.005  0.005  0.005]
Vector 4 in the group:
Before:  [33.901 54.     0.006  0.007  0.008] After:  [33.907  0.004  0.005  0.005  0.005]
Vector 5 in the group:
Before:  [34.19  44.     0.003  0.     0.007] After:  [34.195  0.004  0.005  0.005  0.005]
Vector 6 in the group:
Before:  [34.472 88.     0.007  0.005  0.006] After:  [34.482  0.004  0.005  0.005  0.005]
Vector 7 in the group:
Before:  [34.169  5.     0.003  0.001  0.   ] After:  [34.17   0.004  0.005  0.005  0.005]
Vector 8 in the group:
Before:  [34.381 61.     0.001  0.005  0.008] After:  [34.388  0.004  0.005  0.005  0.005]
Vector 9 in the group:
Before:  [34.234 17.     0.009  0.004  0.007] After:  [34.236  0.004  0.005  0.005  0.00

Before:  [73.114 64.     0.008  0.008  0.005] After:  [73.121  0.008  0.005  0.005  0.005]
Vector 22 in the group:
Before:  [72.538 82.     0.004  0.003  0.005] After:  [72.548  0.008  0.005  0.005  0.005]
Vector 23 in the group:
Before:  [72.803 57.     0.009  0.001  0.005] After:  [72.81   0.008  0.005  0.005  0.005]
Vector 24 in the group:
Before:  [72.639 72.     0.006  0.003  0.01 ] After:  [72.647  0.008  0.005  0.005  0.005]
Vector 25 in the group:
Before:  [73.149 40.     0.009  0.007  0.001] After:  [73.154  0.008  0.005  0.005  0.005]
Vector 26 in the group:
Before:  [73.114  6.     0.005  0.002  0.002] After:  [73.114  0.008  0.005  0.005  0.005]
Vector 27 in the group:
Before:  [72.667 89.     0.005  0.007  0.005] After:  [72.677  0.008  0.005  0.005  0.005]
Vector 28 in the group:
Before:  [72.705 40.     0.008  0.003  0.006] After:  [72.709  0.008  0.005  0.005  0.005]
Vector 29 in the group:
Before:  [72.566 53.     0.006  0.     0.004] After:  [72.572  0.008  0.005  0.0